# Strategy analysis example

Debugging a strategy can be time-consuming. FreqTrade offers helper functions to visualize raw data.

## Setup

In [1]:
%matplotlib inline
import os
from pathlib import Path
# Change directory
# Modify this cell to insure that the output shows the correct path.
# Define all paths relative to the project root shown in the cell output
project_root = "/home/cryo/freqtrade"
i=0
try:
    os.chdirdir(project_root)
    assert Path('LICENSE').is_file()
except:
    while i<4 and (not Path('LICENSE').is_file()):
        os.chdir(Path(Path.cwd(), '../'))
        i+=1
    project_root = Path.cwd()
print(Path.cwd())

# Customize these according to your needs.

# Define some constants
timeframe = "1m"
# Name of the strategy class
strategy_name = 'MLStrategy'
# Path to user data
user_data_dir = Path('user_data')
# Location of the strategy
strategy_location = user_data_dir / 'strategies'
# Location of the data
data_location = Path(user_data_dir, 'data', 'binance')
# Pair to analyze - Only use one pair here
pair = "BTC_USDT"

/home/cryo/freqtrade


In [2]:
# Load data using values set above
from freqtrade.data.history import load_pair_history

candles = load_pair_history(datadir=data_location,
                            timeframe=timeframe,
                            pair=pair)

# Confirm success
print("Loaded " + str(len(candles)) + f" rows of data for {pair} from {data_location}")
# candles.head()
candles.tail()

Loaded 43200 rows of data for BTC_USDT from user_data/data/binance


date     open     high      low    close     volume
43195 2019-11-14 21:45:00+00:00  8665.73  8666.08  8664.50  8664.50   9.772810
43196 2019-11-14 21:46:00+00:00  8664.86  8665.84  8662.64  8662.64  10.064353
43197 2019-11-14 21:47:00+00:00  8664.21  8664.88  8662.67  8663.67   6.865387
43198 2019-11-14 21:48:00+00:00  8663.25  8667.50  8662.05  8665.03   9.376453
43199 2019-11-14 21:49:00+00:00  8665.03  8666.34  8663.27  8665.80   9.811399

## Load and run strategy
* Rerun each time the strategy file is changed

### Display the trade details

* Note that using `data.head()` would also work, however most indicators have some "startup" data at the top of the dataframe.
* Some possible problems
    * Columns with NaN values at the end of the dataframe
    * Columns used in `crossed*()` functions with completely different units
* Comparison with full backtest
    * having 200 buy signals as output for one pair from `analyze_ticker()` does not necessarily mean that 200 trades will be made during backtesting.
    * Assuming you use only one condition such as, `df['rsi'] < 30` as buy condition, this will generate multiple "buy" signals for each pair in sequence (until rsi returns > 29). The bot will only buy on the first of these signals (and also only if a trade-slot ("max_open_trades") is still available), or on one of the middle signals, as soon as a "slot" becomes available.  


In [3]:
# Load strategy using values set above
from freqtrade.resolvers import ExchangeResolver, StrategyResolver
from freqtrade.configuration import Configuration
from freqtrade.state import RunMode
from freqtrade.data.dataprovider import DataProvider
from freqtrade.strategy.interface import IStrategy

config = Configuration.from_files(["config.json"])
exchange = ExchangeResolver(config['exchange']['name'], config, False).exchange
dataprovider = DataProvider(config, exchange)
IStrategy.dp = dataprovider
# dataframe = dataprovider.historic_ohlcv(pair)
strategy = StrategyResolver({'strategy': strategy_name,
                            'user_data_dir': user_data_dir,
                            'strategy_path': strategy_location}).strategy

# Generate buy/sell signals using strategy
df = strategy.analyze_ticker(candles, {'pair': pair})

2019-12-08 15:29:25,831 - freqtrade.loggers - INFO - Verbosity set to 0
2019-12-08 15:29:25,834 - freqtrade.configuration.configuration - INFO - Using user-data directory: /home/cryo/freqtrade/user_data ...
2019-12-08 15:29:25,837 - freqtrade.configuration.configuration - INFO - Using data directory: /home/cryo/freqtrade/user_data/data/binance ...
2019-12-08 15:29:25,840 - freqtrade.configuration.check_exchange - INFO - Checking exchange...
2019-12-08 15:29:25,842 - freqtrade.configuration.check_exchange - INFO - Exchange "binance" is officially supported by the Freqtrade development team.
2019-12-08 15:29:25,850 - freqtrade.configuration.configuration - INFO - Using pairlist from configuration.
2019-12-08 15:29:25,852 - freqtrade.exchange.exchange - INFO - Instance is running with dry_run enabled
2019-12-08 15:29:25,854 - freqtrade.exchange.exchange - INFO - Applying additional ccxt config: {'enableRateLimit': True}
2019-12-08 15:29:25,868 - freqtrade.exchange.exchange - INFO - Applyi

init


2019-12-08 15:29:28,491 - freqtrade.data.converter - INFO - Missing data fillup for BTC/USDT: before: 43057 - after: 43200
2019-12-08 15:29:32,386 - ML Strategy - INFO - parsing ./user_data/news/20191102141037/news.bitcoin.com/feed/index.html
2019-12-08 15:29:32,479 - ML Strategy - INFO - parsing ./user_data/news/20191020204956/news.bitcoin.com/feed/index.html
2019-12-08 15:29:32,575 - ML Strategy - INFO - parsing ./user_data/news/20191031211536/news.bitcoin.com/feed/index.html
2019-12-08 15:29:32,662 - ML Strategy - INFO - parsing ./user_data/news/20191107130611/news.bitcoin.com/feed/index.html
2019-12-08 15:29:32,722 - ML Strategy - INFO - parsing ./user_data/news/20191101165152/news.bitcoin.com/feed/index.html
2019-12-08 15:29:32,853 - ML Strategy - INFO - parsing ./user_data/news/20191028175644/news.bitcoin.com/feed/index.html
2019-12-08 15:29:33,014 - ML Strategy - INFO - parsing ./user_data/news/20191105100233/news.bitcoin.com/feed/index.html
2019-12-08 15:29:33,107 - ML Strategy

2019-12-08 15:29:43,295 - ML Strategy - INFO - Got alfa 0.9992 for candle at 2019-11-04 01:01:00+00:00
2019-12-08 15:29:43,366 - ML Strategy - INFO - Got alfa 0.9995 for candle at 2019-11-03 22:03:00+00:00
2019-12-08 15:29:43,453 - ML Strategy - INFO - Got alfa 0.9859 for candle at 2019-11-04 08:30:00+00:00
2019-12-08 15:29:43,576 - ML Strategy - INFO - Got alfa 0.9989 for candle at 2019-11-04 04:01:00+00:00
2019-12-08 15:29:43,719 - ML Strategy - INFO - Got alfa 0.9992 for candle at 2019-11-04 01:01:00+00:00
2019-12-08 15:29:43,781 - ML Strategy - INFO - Got alfa 0.9995 for candle at 2019-11-03 22:03:00+00:00
2019-12-08 15:29:43,868 - ML Strategy - INFO - Got alfa 0.9992 for candle at 2019-11-03 19:10:00+00:00
2019-12-08 15:29:43,988 - ML Strategy - INFO - Got alfa 0.9983 for candle at 2019-11-03 16:11:00+00:00
2019-12-08 15:29:44,100 - ML Strategy - INFO - Got alfa 0.9986 for candle at 2019-11-03 11:50:00+00:00
2019-12-08 15:29:44,187 - ML Strategy - INFO - Got alfa 0.9966 for candle

train:  [ 0.2686542   0.26132459  0.28527458  0.27042108  0.00498451 -0.28782141
  0.11866994  0.71896295  0.9001233   1.          0.27557003  0.3002132
  0.00522741  0.02124694  0.9985    ] 0.023698224597778397


2019-12-08 15:29:48,307 - freqtrade.resolvers.iresolver - INFO - Using resolved strategy MLStrategy from '/home/cryo/freqtrade/user_data/strategies/ml_strategy.py'...
2019-12-08 15:29:48,309 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using minimal_roi: {'80': 0.02, '40': 0.03, '20': 0.04, '0': 0.05}
2019-12-08 15:29:48,313 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using ticker_interval: 1m
2019-12-08 15:29:48,315 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using stoploss: -0.9
2019-12-08 15:29:48,323 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using trailing_stop: False
2019-12-08 15:29:48,325 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using trailing_stop_positive: 0.01
2019-12-08 15:29:48,328 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using trailing_stop_positive_offset: 0.02
2019-12-08 15:29:48,331 - freqtrade.resolvers.strategy_resolver - INFO - Strategy using trailing_only_offset_is_reached: Fa

Model fitted using dataframe of length = 32399 during 16.733030796051025 seconds with testing score =  -1.2144000687220684


2019-12-08 15:29:51,997 - ML Strategy - INFO - parsing https://news.bitcoin.com/feed/
2019-12-08 15:29:53,456 - ML Strategy - INFO - Got alfa 0.9998 for candle at 2019-11-14 21:49:00+00:00
2019-12-08 15:29:53,575 - ML Strategy - INFO - Got alfa 0.9984 for candle at 2019-11-14 21:49:00+00:00
2019-12-08 15:29:53,719 - ML Strategy - INFO - Got alfa 0.9984 for candle at 2019-11-14 21:49:00+00:00
2019-12-08 15:29:53,859 - ML Strategy - INFO - Got alfa 0.998 for candle at 2019-11-14 21:49:00+00:00
2019-12-08 15:29:53,930 - ML Strategy - INFO - Got alfa 0.9996 for candle at 2019-11-14 21:49:00+00:00
2019-12-08 15:29:54,077 - ML Strategy - INFO - Got alfa 0.9994 for candle at 2019-11-14 21:49:00+00:00
2019-12-08 15:29:54,177 - ML Strategy - INFO - Got alfa 0.9982 for candle at 2019-11-14 21:49:00+00:00
2019-12-08 15:29:54,287 - ML Strategy - INFO - Got alfa 0.9996 for candle at 2019-11-14 21:49:00+00:00
2019-12-08 15:29:54,503 - ML Strategy - INFO - Got alfa 0.9999 for candle at 2019-11-14 21:

predict:  [ 0.2686542   0.26132459  0.28527458  0.27042108  0.00498451 -0.28782141
  0.11866994  0.71896295  0.9001233   1.          0.27557003  0.3002132
  0.00522741  0.02124694  0.999     ] 0.022146045378748862


In [5]:
from plotly.subplots import make_subplots
from plotly.offline import plot
import plotly.graph_objects as go

data = df.set_index('date', drop=False)


data_red = data['2019-10-15':'2019-10-26']
fig = go.Figure()
fig2 = go.Figure()
fig2.add_trace(go.Scatter(x=data_red.date, y=data_red.close, name='close'))
fig2.add_trace(go.Scatter(x=data_red.date, y=data_red.close, name='sentiment'))
# fig2.add_trace(go.Scatter(x=data_red.date, y=data_red['macd'], name='macd'))
# fig2.add_trace(go.Scatter(x=data_red.date, y=data_red.minus_di, name='minus_di'))
# fig2.add_trace(go.Scatter(x=data_red.date, y=data_red['rsi'], name='rsi'))
# fig2.add_trace(go.Scatter(x=data_red.date, y=data_red.fastd, name='fastd'))
# fig2.add_trace(go.Scatter(x=data_red.date, y=data_red.fastk, name='fastk'))
# fig2.add_trace(go.Scatter(x=data_red.date, y=data_red.sar, name='sar'))
# fig2.add_trace(go.Scatter(x=data_red.date, y=data_red['sma'], name='sma'))
# fig2.add_trace(go.Scatter(x=data_red.date, y=data_red.TRANGE, name='TRANGE'))
fig.add_trace(go.Scatter(x=data_red.date, y=data_red.perc_change, name='change, %'))
fig.add_trace(go.Scatter(x=data_red.date, y=data_red.future_perc_change, name='future change, %'))

# print(data_red.keys())

fig2.show()
fig.show()

## Load existing objects into a Jupyter notebook

The following cells assume that you have already generated data using the cli.  
They will allow you to drill deeper into your results, and perform analysis which otherwise would make the output very difficult to digest due to information overload.

### Load backtest results to pandas dataframe

Analyze a trades dataframe (also used below for plotting)

In [ ]:
from freqtrade.data.btanalysis import load_backtest_data

# Load backtest results
trades = load_backtest_data(user_data_dir / "backtest_results/backtest-result-TunedTA.json")

# Show value-counts per pair
trades.groupby("pair")["sell_reason"].value_counts()

### Load live trading results into a pandas dataframe

In case you did already some trading and want to analyze your performance

In [ ]:
from freqtrade.data.btanalysis import load_trades_from_db

# Fetch trades from database
# trades = load_trades_from_db("sqlite:///tradesv3.sqlite")

# Display results
trades.groupby("pair")["sell_reason"].value_counts()

## Analyze the loaded trades for trade parallelism
This can be useful to find the best `max_open_trades` parameter, when used with backtesting in conjunction with `--disable-max-market-positions`.

`analyze_trade_parallelism()` returns a timeseries dataframe with an "open_trades" column, specifying the number of open trades for each candle.

In [ ]:
from freqtrade.data.btanalysis import analyze_trade_parallelism

# Analyze the above
parallel_trades = analyze_trade_parallelism(trades, '5m')


parallel_trades.plot()

## Plot results

Freqtrade offers interactive plotting capabilities based on plotly.

In [ ]:
from freqtrade.plot.plotting import  generate_candlestick_graph
# Limit graph period to keep plotly quick and reactive

data_red = data['2019-10-15':'2019-11-14']
# print(data_red.head())
# Generate candlestick graph
graph = generate_candlestick_graph(pair=pair,
                                   data=data_red,
                                   trades=trades,
                                   indicators1=['close', 'future_close'],
                                   indicators2=['rsi']
                                  )




In [ ]:
# Show graph inline
graph.show()

# Render graph in a seperate window
# graph.show(renderer="browser")


Feel free to submit an issue or Pull Request enhancing this document if you would like to share ideas on how to best analyze the data.